<a href="https://colab.research.google.com/github/carlschroedl/computational-redistricting/blob/main/wisconsin_data_preprocessing.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [56]:
# Download the WI state LTSB's 2020 census data aggregated by ward 
# https://data-ltsb.opendata.arcgis.com/datasets/2020-us-census-data-by-ward/explore
!curl --output '2020_US_Census_Data_by_Ward.zip' -O 'https://opendata.arcgis.com/api/v3/datasets/df0ddd9a49394a0a83867b4db196509f_0/downloads/data?format=shp&spatialRefId=3857'

  % Total    % Received % Xferd  Average Speed   Time    Time     Time  Current
                                 Dload  Upload   Total   Spent    Left  Speed
100 15.3M    0 15.3M    0     0  17.2M      0 --:--:-- --:--:-- --:--:-- 17.1M


In [57]:
# Download the WI state LTSB's election data aggregated by 2020 ward.

#############################################################################
# Note: this file contains old (2010) census data for the wards
# This will be replaced with 2020 census data prior to analysis
#############################################################################

# https://data-ltsb.opendata.arcgis.com/datasets/2012-2020-election-data-with-2020-wards/explore
!curl --output '2012-2020_Election_Data_with_2020_Wards.zip' -O 'https://opendata.arcgis.com/api/v3/datasets/f67c2e7f43bb432687b4a42bee50a16c_0/downloads/data?format=shp&spatialRefId=3857'  

  % Total    % Received % Xferd  Average Speed   Time    Time     Time  Current
                                 Dload  Upload   Total   Spent    Left  Speed
100 21.5M    0 21.5M    0     0  21.0M      0 --:--:--  0:00:01 --:--:-- 21.0M


In [68]:
!pip install geopandas matplotlib gerrychain maup folium

In [86]:
import os
import geopandas
import pandas
import matplotlib.pyplot as plt
import numpy as np
import gerrychain
import maup
from IPython.display import display, Markdown
from pprint import pprint
import folium
import json

In [60]:
census_data_2020 = geopandas.read_file('2020_US_Census_Data_by_Ward.zip')

In [61]:
# inspect census data
print(census_data_2020.info())
print(census_data_2020['GEOID'].head())
print(census_data_2020['WARDID'].head())
print(set(census_data_2020['GEOID']) == set(census_data_2020['WARDID']))


<class 'geopandas.geodataframe.GeoDataFrame'>
RangeIndex: 7136 entries, 0 to 7135
Data columns (total 39 columns):
 #   Column      Non-Null Count  Dtype   
---  ------      --------------  -----   
 0   FID         7136 non-null   int64   
 1   GEOID       7136 non-null   object  
 2   WARDID      7136 non-null   object  
 3   CNTY_FIPS   7136 non-null   object  
 4   CNTY_NAME   7136 non-null   object  
 5   MCD_FIPS    7136 non-null   object  
 6   MCD_NAME    7136 non-null   object  
 7   COUSUBFP    7136 non-null   object  
 8   LSAD        7136 non-null   object  
 9   CTV         7136 non-null   object  
 10  ASM         7136 non-null   object  
 11  SEN         7136 non-null   object  
 12  CON         7136 non-null   object  
 13  LABEL       7136 non-null   object  
 14  STR_WARDS   7136 non-null   object  
 15  DISTRICT    7136 non-null   object  
 16  PERSONS     7136 non-null   int64   
 17  HISPANIC    7136 non-null   int64   
 18  WHITE       7136 non-null   int64   
 19

In [62]:
election_data = geopandas.read_file('2012-2020_Election_Data_with_2020_Wards.zip')

In [100]:
display(Markdown('# Wards in election data but not in census data'))
election_only_wards = set(election_data['GEOID'].to_list()) - set(census_data_2020['GEOID'].to_list())
print(len(election_only_wards))
election_only_wards_df = election_data[election_data['GEOID'].isin(election_only_wards)]

m = folium.Map(location=[44.5, -89.5], zoom_start=7, tiles='CartoDB positron')

for _, r in election_only_wards_df.to_crs(epsg=4326).iterrows():
    # Without simplifying the representation of each borough,
    # the map might not be displayed
    # sim_geo = gpd.GeoSeries(r['geometry']).simplify(tolerance=0.001)
    sim_geo = geopandas.GeoSeries(r['geometry'])
    geo_j = sim_geo.to_json()
    geo_j = folium.GeoJson(data=geo_j,
                           style_function=lambda x: {'fillColor': 'orange'})
    folium.Popup(r['GEOID']).add_to(geo_j)
    geo_j.add_to(m)

m

# Wards in election data but not in census data

86


In [103]:
census_only_wards = set(census_data_2020['GEOID'].to_list()) - set(election_data['GEOID'].to_list())   
display(Markdown(('# Wards in census data but not in election data')))
print(len(census_only_wards))
census_only_wards_df = census_data_2020[census_data_2020['GEOID'].isin(census_only_wards)]

m = folium.Map(location=[44.5, -89.5], zoom_start=7, tiles='CartoDB positron')

for _, r in census_only_wards_df.to_crs(epsg=4326).iterrows():
    # Without simplifying the representation of each borough,
    # the map might not be displayed
    # sim_geo = gpd.GeoSeries(r['geometry']).simplify(tolerance=0.001)
    sim_geo = geopandas.GeoSeries(r['geometry'])
    geo_j = sim_geo.to_json()
    geo_j = folium.GeoJson(data=geo_j,
                           style_function=lambda x: {'color': 'yellow', 'fillColor': 'green'})
    folium.Popup(r['GEOID']).add_to(geo_j)
    geo_j.add_to(m)

m


# Wards in census data but not in election data

144


In [104]:
display(Markdown('# Both '))
m = folium.Map(location=[44.5, -89.5], zoom_start=7, tiles='CartoDB positron')

for _, r in census_only_wards_df.to_crs(epsg=4326).iterrows():
    # Without simplifying the representation of each borough,
    # the map might not be displayed
    # sim_geo = gpd.GeoSeries(r['geometry']).simplify(tolerance=0.001)
    sim_geo = geopandas.GeoSeries(r['geometry'])
    geo_j = sim_geo.to_json()
    geo_j = folium.GeoJson(data=geo_j,
                           style_function=lambda x: {'color': 'yellow', 'fillColor': 'green'})
    folium.Popup(r['GEOID']).add_to(geo_j)
    geo_j.add_to(m)

for _, r in election_only_wards_df.to_crs(epsg=4326).iterrows():
    # Without simplifying the representation of each borough,
    # the map might not be displayed
    # sim_geo = gpd.GeoSeries(r['geometry']).simplify(tolerance=0.001)
    sim_geo = geopandas.GeoSeries(r['geometry'])
    geo_j = sim_geo.to_json()
    geo_j = folium.GeoJson(data=geo_j,
                           style_function=lambda x: {'fillColor': 'orange'})
    folium.Popup(r['GEOID']).add_to(geo_j)
    geo_j.add_to(m)

m


# Both 

In [66]:
try:
  maup.doctor(election_data)
except AssertionError as e:
  print(e)

  1%|          | 43/7078 [00:00<00:41, 170.92it/s]


TopologicalError: ignored

In [ ]:
len(election_data['geometry'])

In [ ]:
import warnings; warnings.filterwarnings('ignore', 'GeoSeries.isna', UserWarning)
maup.progress.enabled = True
without_overlaps_or_gaps = maup.autorepair(election_data)



In [ ]:
without_overlaps_or_gaps.to_file('repaired_2012-2020_Election_Data_with_2020_Wards.zip')

In [ ]:
election_data['geometry'] = without_overlaps_or_gaps

In [ ]:
try:
  maup.doctor(election_data)
except AssertionError as e:
  print(e)

In [ ]:
len(election_data['geometry'])

In [ ]:
print(election_data.info(verbose=True, show_counts=True, null_counts=True))
election_data.plot()

#graph = gerrychain.Graph.from_geodataframe(without_overlaps_or_gaps_df)
# print(state_election_data.info(verbose=True, null_counts=True))
# print('total population')
# print(state_election_data['PERSONS'].sum())
# graph = gerrychain.Graph.from_file('2012-2020_Election_Data_with_2020_Wards.zip')

#print(list(state_election_data.columns)[0:20])
#print(state_election_data['GEOID'].head())

In [ ]:
state_election_ward_ids = set(state_election_data['GEOID'])
state_ward_ids = set(wards['GEOID'])
wards_only_ward_ids = state_ward_ids - state_election_ward_ids
print(len(wards_only_ward_ids))
state_election_only_ward_ids = state_election_ward_ids - state_ward_ids
print(len(state_election_only_ward_ids))

In [ ]:
print(len([(1056, 1153), (5177, 5181), (4322, 4326), (795, 814), (1956, 1957), (4541, 4542), (2850, 2851), (1805, 1875), (586, 800), (5859, 5861), (6902, 6915), (793, 811), (5176, 5181), (5626, 5627), (5519, 5570), (6066, 6082), (2260, 2261), (5172, 5173), (5453, 5465), (5766, 5770), (5820, 5834), (6964, 6965), (5103, 5149), (6910, 6928), (1056, 1065), (2693, 2785), (1407, 1418), (2511, 2545), (2955, 3014), (5407, 5436), (5524, 5531), (3021, 3023), (824, 826), (1336, 1391), (1360, 1410), (2062, 2063), (5746, 5747), (6864, 6867), (2149, 2152), (5001, 5031), (2337, 2338), (3890, 3895), (2775, 2780), (5710, 5721), (2113, 2119), (3019, 3023), (43, 57), (5327, 5328), (1814, 1815), (4970, 4971), (3900, 3965), (5524, 5533), (6920, 6921), (5755, 5759), (1380, 1409), (1041, 1092), (2760, 2788), (2836, 2837), (83, 89), (493, 531), (1058, 1071), (5457, 5499), (475, 476), (140, 149), (1740, 1742), (5172, 5174), (93, 147), (1711, 1716), (2148, 2152), (3882, 3914), (4968, 4971), (1058, 1099), (4562, 4612), (5452, 5465), (6785, 6828), (2864, 2881), (2284, 2308), (3022, 3023), (1056, 1066), (3906, 3907), (5568, 5631), (6722, 6723), (6911, 6932), (2007, 2008), (2131, 2132), (2631, 2633), (85, 89), (2266, 2267), (1741, 1742), (6684, 6812), (6749, 6752), (825, 826), (1053, 1153), (6859, 6868), (6116, 6307), (2847, 2849), (4900, 5308), (590, 606), (5342, 5390), (716, 762), (1059, 1098), (6717, 6718), (474, 476), (2525, 2550), (6785, 6821), (1341, 1442), (1966, 1967), (3905, 3910), (3998, 3999), (5518, 5570), (4730, 4748), (2848, 2849), (2846, 2849), (4179, 4284), (2966, 2971), (5468, 5475), (5712, 5721), (551, 552), (6615, 6712), (87, 89), (6599, 6606), (276, 278), (5175, 5181), (1041, 1153), (3049, 3050), (3074, 3075), (1041, 1068), (1115, 1123), (3020, 3023), (82, 89), (5165, 5166), (5178, 5181), (1062, 1151), (3922, 3940), (5552, 5565), (5520, 5564), (2032, 2038), (2179, 2194), (1259, 1268), (4898, 5307), (6735, 6736), (4160, 4315), (84, 89), (5110, 5111), (6684, 6813), (6588, 6601), (1024, 1106), (2763, 2775), (6129, 6134), (81, 89), (1958, 2040), (2027, 2030), (4460, 4490), (447, 448), (1343, 1344), (5524, 5530), (2490, 2830), (2886, 2887), (844, 1198), (4324, 4326), (6901, 6912), (108, 109), (6785, 6820), (5653, 5673), (7015, 7038), (4883, 4889), (1058, 1091), (4969, 4971), (6785, 6825), (944, 948), (2031, 2032), (2336, 2338), (1663, 1802), (3882, 3932), (4296, 4303), (5569, 5631), (6191, 6225), (5711, 5721), (4453, 4454), (6900, 6914), (1824, 1875), (1965, 1967), (3885, 3975), (830, 831), (1854, 1855), (4686, 4687), (6983, 7007), (5858, 5861), (4563, 4564), (455, 457), (2017, 2018), (2369, 2421), (86, 89), (5131, 5137), (5402, 5403), (1062, 1094), (789, 790), (2537, 2607), (1057, 1070), (5099, 5148), (2154, 2169), (1944, 1945), (4437, 4452), (5524, 5532), (4323, 4326), (1872, 1876), (6883, 6919), (4048, 4088), (2043, 2044), (2688, 2690)]))
wards[~wards['GEOID'].isin(wards_only_ward_ids)].plot()
# wards_only_ward_ids = pandas.DataFrame({
#     'GEOID': np.array(list(wards_only_ward_ids), dtype=object)
# })

# print(wards_only_ward_ids.info())
# outlier_wards = pandas.merge(wards, state_election_data, on='GEOID', how = 'outer')
# print(len(outlier_wards))
# outlier_wards.plot()
# print(wards_only_ward_ids)